Generation from multiple models
===========================

This notebook introduces the AREnsembleGenerator class and some of the required functionality from pbind.py.
Pbinds come from SuperCollider's [Stream-Pattern-Event](http://doc.sccode.org/Tutorials/Streams-Patterns-Events1.html) system.

In [ ]:
pip install git+https://github.com/k-tonal/mimikit@berlach

In [2]:
import librosa
import soundfile as sf
import torch
import numpy as np
from mimikit.generation.pbind import Event, Pbind, Pseq, Prand, Pwhite, inf
from mimikit import NeptuneConnector
from mimikit.freqnet import FreqNet
from mimikit import get_trainer
from mimikit.data import Database
from mimikit.generation.argenerator import AREnsembleGenerator

In [4]:
# get the models from which you want to generate from neptune

nep_con = NeptuneConnector(user="k-tonal",
                           setup=dict(db="data-and-base-notebooks/DAT-32",
                                      mod1="experiment-1/EX1-40",
                                      mod2="experiment-1/EX1-42",
                                      mod3="experiment-1/EX1-46",
                                      mod4="experiment-1/EX1-38",
                                      mod5="experiment-1/EX1-50",
                                      mod6="experiment-1/EX1-53",
                                      mod7="experiment-1/EX1-68",
                                      mod8="experiment-1/EX1-71"
                                     ))

for key in nep_con.setup.keys():
    if key is not 'db':
        nep_con.download_experiment(key, artifacts="states/")

# grab the required data
db = nep_con.download_database("db", "pansori.h5", destination="./dbs")


In [3]:
# load the models (in this case alway at epoch 99)
# db = Database('dbs/pansori.h5')

data = db.fft.get(db.metadata.iloc[0:])
models = [ FreqNet.load_from_checkpoint('./' + exp + '/states/epoch=99.ckpt', data_object=data) 
           for exp in ['EX1-40', 'EX1-42', 'EX1-46', 'EX1-38', 'EX1-50', 'EX1-53', 'EX1-68', 'EX1-71']]


Generating
----------------

The generation works by creating a pattern that provides a stream of events to the
AREnsembleGenerator.  There are several types of pattern generators.  If you are not
familiar with Pbind patterns this is probably confusing at first.  Some examples are
given below so just hang in there for now.

The most useful ones for the AREnsembleGenerator are:

- Pseq - cycles through a list of values
- Prand - randomly selects from a list of values
- Pwhite - generates random numbers in a given range
- Pn - repeat a value n times
- Pbind - combines several patterns to create a pattern of Events

The generator expects a events that have the following fields:

- 'type' - this can be 'model', 'rest', 'prompt', 'insert' (this field is required)
- 'dur'  - the duration (in seconds) that the output for this event takes (required if 'n_frames' is not provided)
- 'n_frames' - the number of frames this event will output (use either this or use 'dur' to specify in seconds)

If the type of the even is 'model' a field that specifies which model to be used has to be given

- 'model' - this should be a pattern that yields integers.  This is the index into the list of models

If the type is prompt

- 'start_frame' - start frame in the data to get the prompt
- 'start' - start point in seconds in the data to get the prompt
- 'data' - the data from which to pick the prompt (optional - a data argument is given to the generator)

There are some additional optional fields for the 'model' type event

- 'noise' - adds some noise to the input of the model. Can prevent repetitive model outputs
- 'decay' - multiplies model output at each step. 


In [ ]:
import itertools as itools
import random


class Pattern:

    def __init__(self, lst, repeats=1):
        self.lst = lst
        self.repeats = repeats

    def __iter__(self):
        for _ in itools.repeat(None, self.repeats) if self.repeats is not None \
                else itools.repeat(None):
            self.reset()
            for x in self.lst:
                if isinstance(x, Pattern):
                    for y in x:
                        yield y
                else:
                    yield x

    def reset(self):
        pass

    def asStream(self):
        return iter(self)


class Pseq(Pattern):
    pass


class Pshuffle(Pattern):
    def reset(self):
        random.shuffle(self.lst)


class Pchoice(Pattern):
    def __init__(self, lst, repeats=1):
        self._lst = lst
        self.lst = lst
        self.repeats = repeats

    def reset(self):
        self.lst = [random.choice(self._lst) for _ in range(len(self.lst))]


class Pconst(Pattern):
    def __init__(self, item, repeats=1):
        super().__init__([item], repeats)


class Pybind(Pattern):
    def __init__(self, **kwargs):
        self.lst = [{k: iter(v) if isinstance(v, Pattern) else iter(Pconst(v, None))
                     for k, v in kwargs.items()}]
        self.repeats = None

    def __iter__(self):
        iterator = super().__iter__()
        for event in iterator:
            try:
                yield {k: next(v) for k, v in event.items()}
            except StopIteration:
                break


class Pbind(Pybind):
    def __init__(self, *args):
        iterator = zip(range(0, len(args) - 1, 2), range(1, len(args), 2))
        super().__init__(**{args[i]: args[j] for i, j in iterator})


# for x in Pattern([0,9, Pattern([8, 2, 4], repeats=3), 3], repeats=2):
#   print(x)

# list(Pattern([8, None, Pconst(1, 3)], repeats=3))
list(Pbind('type', 'model', 'model', Pseq([0, 1, 2], repeats=2), 'dur', Pshuffle([1, 2], repeats=4)))


In [7]:
# some Pattern examples

print('Pseq:')

# Pseq(list, n_repetitions)
# in this case n_repitions is set to inf which creates an infinite stream.
# The default for n_repetitions is one.  Which means the stream goes exactly one time through the list.

stream = Pseq([0, 10, 2, 1], inf).asStream()

for k in range(10):
    print(stream.next())

print('Prand:')

stream = Prand([3.5, 0.5, 1.0], inf).asStream()

for k in range(10):
    print(stream.next())
    
# patterns can be nested

print('nested pattern:')

stream = Prand([Pseq([1, 2]), Prand([100, 102]), Pwhite(-0.2, 0.2, 4)], inf).asStream()

for k in range(20):
    print(stream.next())


Pseq:
0
10
2
1
0
10
2
1
0
10
Prand:
1.0
1.0
3.5
3.5
0.5
1.0
3.5
3.5
3.5
0.5
nested pattern:
1
2
0.04451292608704477
0.09299382205538603
-0.05857848985065903
0.1759985242584995
100
-0.033367372748648316
0.13163449944951333
0.10319519594599663
0.11933230604250944
100
-0.041813619690748316
0.1215578523147886
0.1255075099351804
-0.1483377768575731
102
102
0.14513600073675093
-0.19375044110380235


In [8]:
# Example for a Pbind pattern
# the arguments for the Pbind are key value pairs
# Pbind(key, pattern, key, pattern ...)

# Because Pbinds can be chained they need an event as input.
# Don't worry about this, normaly you don't need to take care about those things.
# this is just to demonstrate what the output of a pbind looks like
ev = Event({})

stream = Pbind('type', 'model', 'model', Prand([0,1,2], 5), 'dur', Prand([0.5, 1.0], inf)).asStream(ev)


# get all items in the stream.
# notice that there are only 5 events (and a None at the end which signals the end of the pattern)
# There are only 5 events because there is a Prand([0,1,2], 5) in the 'model' field.
# The pbind ends when one of the included substreams ends

list(stream)


[{'type': 'model', 'model': 1, 'dur': 0.5},
 {'type': 'model', 'model': 0, 'dur': 1.0},
 {'type': 'model', 'model': 1, 'dur': 0.5},
 {'type': 'model', 'model': 0, 'dur': 0.5},
 {'type': 'model', 'model': 0, 'dur': 0.5},
 None]

In [6]:
# generate output

# First we create the pattern for the model selection
# It is a Pseq with the first element being a Pbind that creates a 'prompt' event
# The second Pbind will randomly select from the models 
# and randomly run the selected model for a number of seconds picked from the 'dur' field

pattern = Pseq([
                Pbind('type', 'prompt', 'n_frames', 64, 'start_frame', Pwhite(0, 13432, 1), 'data', data),
                Pbind('type', 'model',
                      'model', Pseq([0,1,2,3,4,5,6,7], inf),
                      'noise', Prand([0,0.001, 0.005], inf),
                      'dur', Prand([1,4], inf)
                )])

# The AREnsembleGenerator(models, data, duration, pattern, device) arguments:
# models - a list of models
# data - prompt_data
# dur - generate approximately this many seconds of output data

gen = AREnsembleGenerator(models, data, 120, pattern, 'cpu')

output = gen.generate(time_domain=True, hop_size=512)


model generate 43 slice(-16, None, None)
43 2.4845351473922905
model generate 172 slice(-16, None, None)
172 6.478367346938776
model generate 43 slice(-16, None, None)
43 7.476825396825397
model generate 43 slice(-16, None, None)
43 8.47528344671202
model generate 172 slice(-16, None, None)
172 12.469115646258505
model generate 43 slice(-16, None, None)
43 13.467573696145127
model generate 172 slice(-16, None, None)
172 17.461405895691612
model generate 43 slice(-16, None, None)
43 18.459863945578235
model generate 43 slice(-16, None, None)
43 19.458321995464857
model generate 43 slice(-16, None, None)
43 20.45678004535148
model generate 43 slice(-16, None, None)
43 21.4552380952381
model generate 43 slice(-16, None, None)
43 22.453696145124724
model generate 172 slice(-16, None, None)
172 26.44752834467121
model generate 172 slice(-16, None, None)
172 30.441360544217694
model generate 172 slice(-16, None, None)
172 34.435192743764176
model generate 43 slice(-16, None, None)
43 35.4336

In [7]:
from mimikit.utils import audio

audio(output)